In [ ]:
from unsloth import FastLanguageModel
import torch
max_seq_length = 2048 # Choose any! We auto support RoPE Scaling internally!
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit quantization to reduce memory usage. Can be False.


model, tokenizer = FastLanguageModel.from_pretrained(
    #model_name = "unsloth/llama-3-8b-bnb-4bit",
    model_name="/home/walid/Training_checkpoints/Final",
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
==((====))==  Unsloth: Fast Llama patching release 2024.6
   \\   /|    GPU: NVIDIA RTX A4000. Max memory: 15.635 GB. Platform = Linux.
O^O/ \_/ \    Pytorch: 2.3.0+cu118. CUDA = 8.6. CUDA Toolkit = 11.8.
\        /    Bfloat16 = TRUE. Xformers = 0.0.26.post1+cu118. FA = False.
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Unsloth 2024.6 patched 32 layers with 32 QKV layers, 32 O layers and 32 MLP layers.


In [ ]:
model = FastLanguageModel.get_peft_model(
    model,
    r = 16, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 16,
    lora_dropout = 0, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)

Unsloth: Already have LoRA adapters! We shall skip this step.


In [ ]:
alpaca_prompt = """Below is an article that describes a news. Write a response that appropriately completes the request.

### Article:
{}


### Label:
{}"""

EOS_TOKEN = tokenizer.eos_token # Must add EOS_TOKEN
def formatting_prompts_func(examples):
    articles = examples["Article"]
    labels      = examples["label"]
    texts = []
    for Article,Label in zip(articles,labels):
        # Must add EOS_TOKEN, otherwise the generation will go on forever!
        text = alpaca_prompt.format(Article, Label) + EOS_TOKEN
        texts.append(text)
    return { "text" : texts, }
pass

from datasets import load_dataset
url='TheFullDataset.csv'
#i'm only selecting 1000! we should remove that line when real finetuning
dataset = load_dataset("csv", data_files = {"train" : url}, split = "train")
dataset = dataset.map(formatting_prompts_func, batched = True,)
length_dataset=len(dataset)
val_dataset=dataset.select(indices=range(length_dataset-50000,length_dataset))
dataset= dataset.select(indices=range(516000,length_dataset-50000))


In [ ]:
from trl import SFTTrainer
from transformers import TrainingArguments
from unsloth import is_bfloat16_supported

#here we given max_steps 60, we should remove this and let it do mant steps as needed
trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = dataset,
    eval_dataset=val_dataset,
    dataset_text_field = "text",
    max_seq_length = max_seq_length,
    dataset_num_proc = 4,
    packing = False, # Can make training 5x faster for short sequences.
    args = TrainingArguments(
        output_dir="/home/walid/Training_checkpoints/",
        per_device_train_batch_size = 1,
        gradient_accumulation_steps = 4,
        warmup_steps = 5,
        save_steps=5000,
        num_train_epochs=1,
        learning_rate = 5e-5,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.00125,

        lr_scheduler_type = "linear",
        seed = 3407,
    ),

)
        #max_steps = 60,


In [ ]:
trainer_stats = trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs = 1
   \\   /|    Num examples = 263,367 | Num Epochs = 1
O^O/ \_/ \    Batch size per device = 1 | Gradient Accumulation steps = 4
\        /    Total batch size = 4 | Total steps = 65,841
 "-____-"     Number of trainable parameters = 41,943,040


  0%|          | 0/65841 [00:00<?, ?it/s]

{'loss': 1.0672, 'grad_norm': 0.8914993405342102, 'learning_rate': 1e-05, 'epoch': 0.0}
{'loss': 1.0303, 'grad_norm': 0.9815070629119873, 'learning_rate': 2e-05, 'epoch': 0.0}
{'loss': 1.0425, 'grad_norm': 1.0982651710510254, 'learning_rate': 3e-05, 'epoch': 0.0}
{'loss': 1.1328, 'grad_norm': 1.097751498222351, 'learning_rate': 4e-05, 'epoch': 0.0}
{'loss': 0.9365, 'grad_norm': 0.6804267764091492, 'learning_rate': 5e-05, 'epoch': 0.0}
{'loss': 1.2019, 'grad_norm': 0.8389205932617188, 'learning_rate': 4.999924053709217e-05, 'epoch': 0.0}
{'loss': 0.893, 'grad_norm': 1.0356501340866089, 'learning_rate': 4.999848107418434e-05, 'epoch': 0.0}
{'loss': 1.0437, 'grad_norm': 1.029579758644104, 'learning_rate': 4.999772161127651e-05, 'epoch': 0.0}
{'loss': 0.8772, 'grad_norm': 1.2074975967407227, 'learning_rate': 4.9996962148368675e-05, 'epoch': 0.0}
{'loss': 1.3462, 'grad_norm': 0.806399941444397, 'learning_rate': 4.999620268546085e-05, 'epoch': 0.0}
{'loss': 1.1113, 'grad_norm': 0.83673048019

for the last Num examples = 263,367
{'loss': 1.5451, 'grad_norm': 1.7511740922927856, 'learning_rate': 0.0, 'epoch': 1.0}
{'train_runtime': 246138.1865, 'train_samples_per_second': 1.07, 'train_steps_per_second': 0.267, 'train_loss': 1.4085904401790885, 'epoch': 1.0}

In [ ]:
#evaluating Lora adapters (not merged), more computational but more flexible inference.
Evaluation_stats =trainer.evaluate()

In [ ]:
import pandas as pd
df=pd.DataFrame(trainer.state.log_history)
df
df.to_csv('Training_history')

: 

sine the traiing will take q long time can you add bach size

In [ ]:
# alpaca_prompt = Copied from above
FastLanguageModel.for_inference(model) # Enable native 2x faster inference
inputs = tokenizer(
[
    alpaca_prompt.format(
        "LASIK warning controversy sparks debate on telivision on how dangerous it is, and they concluded it is lethal.", # article
        "", # output - leave this blank for generation!
    )
], return_tensors = "pt").to("cuda")

from transformers import TextStreamer
text_streamer = TextStreamer(tokenizer)
_ = model.generate(**inputs, streamer = text_streamer, max_new_tokens = 128)

: 

In [ ]:
#here we only save the adapters!
model.save_pretrained("llama_lora_model") # Local saving
tokenizer.save_pretrained("llama_lora_model")
# model.push_to_hub("your_name/lora_model", token = "...") # Online saving
# tokenizer.push_to_hub("your_name/lora_model", token = "...") # Online saving

('llama_lora_model/tokenizer_config.json',
 'llama_lora_model/special_tokens_map.json',
 'llama_lora_model/tokenizer.json')

In [ ]:

HF_TOKEN="your key here"
model.save_pretrained_merged("/home/walid/Training_checkpoints/NGILlama3", tokenizer, save_method = "merged_16bit",)
model.push_to_hub_merged("a-hamdi/NGILlama3-merged", tokenizer, save_method = "merged_16bit", token = HF_TOKEN)
model.push_to_hub("a-hamdi/NGILlama3", tokenizer, save_method = "lora",token = HF_TOKEN)

Unsloth: Merging 4bit and LoRA weights to 16bit...
Unsloth: Will use up to 16.73 out of 31.04 RAM for saving.


100%|██████████| 32/32 [00:11<00:00,  2.74it/s]


Unsloth: Saving tokenizer... Done.
Unsloth: Saving model... This might take 5 minutes for Llama-7b...
Done.


Unsloth: You are pushing to hub, but you passed your HF username = a-hamdi.
We shall truncate a-hamdi/NGILlama3-merged to NGILlama3-merged


Unsloth: Merging 4bit and LoRA weights to 16bit...
Unsloth: Will use up to 16.93 out of 31.04 RAM for saving.


...

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

Done.
Saved merged model to https://huggingface.co/a-hamdi/NGILlama3-merged


README.md:   0%|          | 0.00/574 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/168M [00:00<?, ?B/s]

Saved model to https://huggingface.co/a-hamdi/NGILlama3
